# Synchronize Annif corpus files against latest YSO

This notebook can be used to update Annif corpus files that have been created using an older version of YSO. It will read the old corpus files, look up YSO URIs in the new YSO version, update their labels in case they have changed, change deprecated URIs to their successors and remove any URIs that are not in the new YSO (should not happen but...).

Requirements:

* jupyter (obviously)
* rdflib

In [2]:
# Parse the current version of YSO

import rdflib
yso = rdflib.Graph()
yso.parse('../vocab/yso-combined-2022-11-02.ttl', format='turtle')
print(len(yso))  # show number of triples

830887


In [3]:
# Define helper functions

import functools
import glob
from rdflib.namespace import RDF, OWL, DCTERMS, SKOS

def parse_tsv(fn):
    with open(fn) as tsvf:
        for line in tsvf:
            line = line.strip()
            if '\t' not in line:
                print("warning: cannot parse line, skipping:", line)
                continue
            uri, label = line.strip().split('\t')    
            uri = uri[1:-1]
            yield (uri, label)

@functools.lru_cache(maxsize=30000)
def concept_label(uri, default, lang):
    labels = yso.preferredLabel(uri, lang=lang)
    if labels:
        return str(labels[0][1])
    else:
        return default

@functools.lru_cache(maxsize=30000)
def replace_concept(subj, lang):
    uri, label = subj
    uri = rdflib.URIRef(uri)
    replacements = list(yso.objects(uri, DCTERMS.isReplacedBy))
    if len(replacements) == 0:
        return [(str(uri), concept_label(uri, label, lang))]
    else:
        print("replacing", uri, "with", ' '.join([str(r) for r in replacements]))
        if len(replacements) > 1:
            print("warning: multiple replacements for", uri)
        return [(str(r), concept_label(r, label, lang)) for r in replacements]

@functools.lru_cache(maxsize=30000)
def check_concept(uri, lang):
    uri = rdflib.URIRef(uri)
    if (uri, RDF.type, SKOS.Concept) not in yso:
        print(uri, "not a skos:Concept")
        return False
    if (uri, OWL.deprecated, True) in yso:
        print(uri, "is deprecated")
        return False
    if concept_label(uri, None, lang) is None:
        print(uri, "has no label")
        return False
    return True


            
def write_tsv(fn, subjects):
    with open(fn, 'w') as tsvf:
        for uri, label in subjects:
            print("<{}>\t{}".format(uri, label), file=tsvf)

def sync_fulltext_dir(pattern, lang):
    for idx, fn in enumerate(glob.glob(pattern)):
        print(fn)
        l = list(parse_tsv(fn))
        #print(l)
        subjects = []
        for subj in l:
            subjects += replace_concept(subj, lang)
        for uri, label in subjects:
            check_concept(uri, lang)
        #print(subjects)
        write_tsv(fn, subjects)


In [7]:
sync_fulltext_dir('../fulltext/kirjastonhoitaja/*/*.tsv', 'fi')

../fulltext/kirjastonhoitaja/all/384515.tsv
../fulltext/kirjastonhoitaja/all/384557.tsv
../fulltext/kirjastonhoitaja/all/384583.tsv
../fulltext/kirjastonhoitaja/all/384590.tsv
../fulltext/kirjastonhoitaja/all/384616.tsv
../fulltext/kirjastonhoitaja/all/384637.tsv
../fulltext/kirjastonhoitaja/all/384651.tsv
../fulltext/kirjastonhoitaja/all/384658.tsv
../fulltext/kirjastonhoitaja/all/384666.tsv
../fulltext/kirjastonhoitaja/all/384668.tsv
../fulltext/kirjastonhoitaja/all/384677.tsv
../fulltext/kirjastonhoitaja/all/384680.tsv
../fulltext/kirjastonhoitaja/all/384681.tsv
../fulltext/kirjastonhoitaja/all/384687.tsv
../fulltext/kirjastonhoitaja/all/384689.tsv
../fulltext/kirjastonhoitaja/all/384694.tsv
../fulltext/kirjastonhoitaja/all/384711.tsv
../fulltext/kirjastonhoitaja/all/384716.tsv
../fulltext/kirjastonhoitaja/all/384720.tsv
../fulltext/kirjastonhoitaja/all/384762.tsv
../fulltext/kirjastonhoitaja/all/384765.tsv
../fulltext/kirjastonhoitaja/all/384810.tsv
../fulltext/kirjastonhoitaja/all

../fulltext/kirjastonhoitaja/all/389241.tsv
../fulltext/kirjastonhoitaja/all/389267.tsv
../fulltext/kirjastonhoitaja/all/389270.tsv
../fulltext/kirjastonhoitaja/all/389329.tsv
../fulltext/kirjastonhoitaja/all/389430.tsv
../fulltext/kirjastonhoitaja/all/389457.tsv
../fulltext/kirjastonhoitaja/all/389471.tsv
../fulltext/kirjastonhoitaja/all/389580.tsv
../fulltext/kirjastonhoitaja/all/389625.tsv
../fulltext/kirjastonhoitaja/all/389691.tsv
../fulltext/kirjastonhoitaja/all/389702.tsv
../fulltext/kirjastonhoitaja/all/389720.tsv
../fulltext/kirjastonhoitaja/all/389738.tsv
../fulltext/kirjastonhoitaja/all/389756.tsv
../fulltext/kirjastonhoitaja/all/389772.tsv
../fulltext/kirjastonhoitaja/all/389777.tsv
../fulltext/kirjastonhoitaja/all/389801.tsv
../fulltext/kirjastonhoitaja/all/389820.tsv
../fulltext/kirjastonhoitaja/all/389847.tsv
../fulltext/kirjastonhoitaja/all/389866.tsv
../fulltext/kirjastonhoitaja/all/389914.tsv
../fulltext/kirjastonhoitaja/all/389944.tsv
../fulltext/kirjastonhoitaja/all

../fulltext/kirjastonhoitaja/all/395311.tsv
../fulltext/kirjastonhoitaja/all/395341.tsv
../fulltext/kirjastonhoitaja/all/395370.tsv
../fulltext/kirjastonhoitaja/all/395420.tsv
../fulltext/kirjastonhoitaja/all/395451.tsv
../fulltext/kirjastonhoitaja/all/395485.tsv
../fulltext/kirjastonhoitaja/all/395492.tsv
../fulltext/kirjastonhoitaja/all/395579.tsv
../fulltext/kirjastonhoitaja/all/395605.tsv
../fulltext/kirjastonhoitaja/all/395606.tsv
../fulltext/kirjastonhoitaja/all/395645.tsv
../fulltext/kirjastonhoitaja/all/395708.tsv
../fulltext/kirjastonhoitaja/all/395711.tsv
../fulltext/kirjastonhoitaja/all/395724.tsv
../fulltext/kirjastonhoitaja/all/395844.tsv
../fulltext/kirjastonhoitaja/all/395885.tsv
../fulltext/kirjastonhoitaja/all/395990.tsv
../fulltext/kirjastonhoitaja/all/396046.tsv
../fulltext/kirjastonhoitaja/all/396125.tsv
../fulltext/kirjastonhoitaja/all/396207.tsv
../fulltext/kirjastonhoitaja/all/396250.tsv
../fulltext/kirjastonhoitaja/all/396336.tsv
../fulltext/kirjastonhoitaja/all

../fulltext/kirjastonhoitaja/all/401672.tsv
../fulltext/kirjastonhoitaja/all/401716.tsv
../fulltext/kirjastonhoitaja/all/401732.tsv
../fulltext/kirjastonhoitaja/all/401744.tsv
../fulltext/kirjastonhoitaja/all/401787.tsv
../fulltext/kirjastonhoitaja/all/401889.tsv
../fulltext/kirjastonhoitaja/all/401892.tsv
../fulltext/kirjastonhoitaja/all/401946.tsv
../fulltext/kirjastonhoitaja/all/401974.tsv
../fulltext/kirjastonhoitaja/all/401978.tsv
../fulltext/kirjastonhoitaja/all/402002.tsv
../fulltext/kirjastonhoitaja/all/402008.tsv
../fulltext/kirjastonhoitaja/all/402036.tsv
../fulltext/kirjastonhoitaja/all/402042.tsv
../fulltext/kirjastonhoitaja/all/402061.tsv
../fulltext/kirjastonhoitaja/all/402096.tsv
../fulltext/kirjastonhoitaja/all/402100.tsv
../fulltext/kirjastonhoitaja/all/402162.tsv
../fulltext/kirjastonhoitaja/all/402169.tsv
../fulltext/kirjastonhoitaja/all/402213.tsv
../fulltext/kirjastonhoitaja/all/402245.tsv
../fulltext/kirjastonhoitaja/all/402287.tsv
../fulltext/kirjastonhoitaja/all

../fulltext/kirjastonhoitaja/all/418003.tsv
../fulltext/kirjastonhoitaja/all/407487.tsv
../fulltext/kirjastonhoitaja/all/407566.tsv
../fulltext/kirjastonhoitaja/all/407601.tsv
../fulltext/kirjastonhoitaja/all/407609.tsv
../fulltext/kirjastonhoitaja/all/407664.tsv
../fulltext/kirjastonhoitaja/all/407812.tsv
../fulltext/kirjastonhoitaja/all/407901.tsv
../fulltext/kirjastonhoitaja/all/407902.tsv
../fulltext/kirjastonhoitaja/all/407929.tsv
../fulltext/kirjastonhoitaja/all/407947.tsv
../fulltext/kirjastonhoitaja/all/407964.tsv
../fulltext/kirjastonhoitaja/all/407970.tsv
../fulltext/kirjastonhoitaja/all/408036.tsv
../fulltext/kirjastonhoitaja/all/408108.tsv
../fulltext/kirjastonhoitaja/all/408120.tsv
../fulltext/kirjastonhoitaja/all/408132.tsv
../fulltext/kirjastonhoitaja/all/408145.tsv
../fulltext/kirjastonhoitaja/all/408163.tsv
../fulltext/kirjastonhoitaja/all/408172.tsv
../fulltext/kirjastonhoitaja/all/408198.tsv


...

../fulltext/kirjastonhoitaja/validate/437270.tsv
../fulltext/kirjastonhoitaja/validate/437295.tsv
../fulltext/kirjastonhoitaja/validate/437300.tsv
../fulltext/kirjastonhoitaja/validate/437310.tsv
../fulltext/kirjastonhoitaja/validate/437313.tsv
../fulltext/kirjastonhoitaja/validate/437340.tsv
../fulltext/kirjastonhoitaja/validate/437350.tsv
../fulltext/kirjastonhoitaja/validate/437352.tsv
../fulltext/kirjastonhoitaja/validate/437358.tsv
../fulltext/kirjastonhoitaja/validate/437383.tsv
../fulltext/kirjastonhoitaja/validate/437402.tsv
../fulltext/kirjastonhoitaja/validate/437409.tsv
../fulltext/kirjastonhoitaja/validate/437428.tsv
../fulltext/kirjastonhoitaja/validate/437435.tsv


../fulltext/kirjastonhoitaja/validate/437437.tsv
../fulltext/kirjastonhoitaja/validate/437444.tsv
../fulltext/kirjastonhoitaja/validate/437445.tsv
../fulltext/kirjastonhoitaja/validate/437446.tsv
../fulltext/kirjastonhoitaja/validate/437448.tsv
../fulltext/kirjastonhoitaja/validate/437452.tsv
../fulltext/kirjastonhoitaja/validate/437457.tsv
../fulltext/kirjastonhoitaja/validate/437462.tsv
../fulltext/kirjastonhoitaja/validate/437467.tsv
../fulltext/kirjastonhoitaja/validate/437472.tsv
../fulltext/kirjastonhoitaja/validate/437480.tsv
../fulltext/kirjastonhoitaja/validate/437492.tsv
../fulltext/kirjastonhoitaja/validate/437503.tsv
../fulltext/kirjastonhoitaja/validate/437531.tsv
../fulltext/kirjastonhoitaja/validate/437552.tsv
../fulltext/kirjastonhoitaja/validate/437556.tsv
../fulltext/kirjastonhoitaja/validate/437558.tsv
../fulltext/kirjastonhoitaja/validate/437563.tsv
../fulltext/kirjastonhoitaja/validate/437565.tsv
../fulltext/kirjastonhoitaja/validate/437575.tsv
../fulltext/kirjasto

../fulltext/kirjastonhoitaja/fulltext-train/388464.tsv
../fulltext/kirjastonhoitaja/fulltext-train/388607.tsv
../fulltext/kirjastonhoitaja/fulltext-train/388627.tsv
../fulltext/kirjastonhoitaja/fulltext-train/388915.tsv
../fulltext/kirjastonhoitaja/fulltext-train/389042.tsv
../fulltext/kirjastonhoitaja/fulltext-train/389239.tsv
../fulltext/kirjastonhoitaja/fulltext-train/389702.tsv
../fulltext/kirjastonhoitaja/fulltext-train/389720.tsv
../fulltext/kirjastonhoitaja/fulltext-train/389801.tsv
../fulltext/kirjastonhoitaja/fulltext-train/389965.tsv
../fulltext/kirjastonhoitaja/fulltext-train/390361.tsv
../fulltext/kirjastonhoitaja/fulltext-train/390592.tsv
../fulltext/kirjastonhoitaja/fulltext-train/390633.tsv
../fulltext/kirjastonhoitaja/fulltext-train/390913.tsv
../fulltext/kirjastonhoitaja/fulltext-train/391003.tsv
../fulltext/kirjastonhoitaja/fulltext-train/391321.tsv
../fulltext/kirjastonhoitaja/fulltext-train/391421.tsv
../fulltext/kirjastonhoitaja/fulltext-train/391572.tsv
../fulltex

../fulltext/kirjastonhoitaja/fulltext-train/414555.tsv
../fulltext/kirjastonhoitaja/fulltext-train/414556.tsv
../fulltext/kirjastonhoitaja/fulltext-train/414582.tsv
../fulltext/kirjastonhoitaja/fulltext-train/414687.tsv
../fulltext/kirjastonhoitaja/fulltext-train/414701.tsv
../fulltext/kirjastonhoitaja/fulltext-train/414807.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415474.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415527.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415611.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415641.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415725.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415771.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415896.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415967.tsv
../fulltext/kirjastonhoitaja/fulltext-train/415980.tsv
../fulltext/kirjastonhoitaja/fulltext-train/416030.tsv
../fulltext/kirjastonhoitaja/fulltext-train/416037.tsv
../fulltext/kirjastonhoitaja/fulltext-train/416286.tsv
../fulltex

../fulltext/kirjastonhoitaja/fulltext-train/427637.tsv
../fulltext/kirjastonhoitaja/fulltext-train/427674.tsv
../fulltext/kirjastonhoitaja/fulltext-train/427703.tsv
../fulltext/kirjastonhoitaja/fulltext-train/427958.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428041.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428062.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428542.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428564.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428581.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428614.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428672.tsv
../fulltext/kirjastonhoitaja/fulltext-train/428814.tsv
../fulltext/kirjastonhoitaja/fulltext-train/429022.tsv
../fulltext/kirjastonhoitaja/fulltext-train/429114.tsv
../fulltext/kirjastonhoitaja/fulltext-train/429180.tsv
../fulltext/kirjastonhoitaja/fulltext-train/429275.tsv
../fulltext/kirjastonhoitaja/fulltext-train/429558.tsv
../fulltext/kirjastonhoitaja/fulltext-train/429702.tsv
../fulltex

In [8]:
sync_fulltext_dir('../fulltext/jyu-theses/fin/*.tsv', 'fi')

../fulltext/jyu-theses/fin/2010-D-22709.tsv
../fulltext/jyu-theses/fin/2010-D-22711.tsv
../fulltext/jyu-theses/fin/2010-D-22712.tsv
../fulltext/jyu-theses/fin/2010-D-22736.tsv
../fulltext/jyu-theses/fin/2010-D-22737.tsv
../fulltext/jyu-theses/fin/2010-D-23021.tsv
../fulltext/jyu-theses/fin/2010-D-23063.tsv
../fulltext/jyu-theses/fin/2010-D-23093.tsv
../fulltext/jyu-theses/fin/2010-D-23241.tsv
../fulltext/jyu-theses/fin/2010-D-23383.tsv
../fulltext/jyu-theses/fin/2010-D-23627.tsv
../fulltext/jyu-theses/fin/2010-D-23630.tsv
../fulltext/jyu-theses/fin/2010-D-24537.tsv
../fulltext/jyu-theses/fin/2010-D-24576.tsv
../fulltext/jyu-theses/fin/2010-D-24951.tsv
../fulltext/jyu-theses/fin/2010-D-24954.tsv
../fulltext/jyu-theses/fin/2010-D-24957.tsv
../fulltext/jyu-theses/fin/2010-D-24958.tsv
../fulltext/jyu-theses/fin/2010-D-24964.tsv
../fulltext/jyu-theses/fin/2010-D-24973.tsv
../fulltext/jyu-theses/fin/2010-D-25207.tsv
../fulltext/jyu-theses/fin/2010-D-25453.tsv
../fulltext/jyu-theses/fin/2010-

../fulltext/jyu-theses/fin/2010-M-24746.tsv
../fulltext/jyu-theses/fin/2010-M-24747.tsv
../fulltext/jyu-theses/fin/2010-M-24749.tsv
../fulltext/jyu-theses/fin/2010-M-24751.tsv
../fulltext/jyu-theses/fin/2010-M-24825.tsv
../fulltext/jyu-theses/fin/2010-M-24831.tsv
../fulltext/jyu-theses/fin/2010-M-24832.tsv
../fulltext/jyu-theses/fin/2010-M-24843.tsv
../fulltext/jyu-theses/fin/2010-M-24851.tsv
../fulltext/jyu-theses/fin/2010-M-24853.tsv
../fulltext/jyu-theses/fin/2010-M-24862.tsv
../fulltext/jyu-theses/fin/2010-M-24876.tsv
../fulltext/jyu-theses/fin/2010-M-24879.tsv
../fulltext/jyu-theses/fin/2010-M-24887.tsv
../fulltext/jyu-theses/fin/2010-M-24888.tsv
../fulltext/jyu-theses/fin/2010-M-24889.tsv
../fulltext/jyu-theses/fin/2010-M-24895.tsv
../fulltext/jyu-theses/fin/2010-M-24899.tsv
../fulltext/jyu-theses/fin/2010-M-24900.tsv
../fulltext/jyu-theses/fin/2010-M-24901.tsv
../fulltext/jyu-theses/fin/2010-M-24902.tsv
../fulltext/jyu-theses/fin/2010-M-24906.tsv
../fulltext/jyu-theses/fin/2010-

../fulltext/jyu-theses/fin/2010-M-36571.tsv
../fulltext/jyu-theses/fin/2010-M-36728.tsv
../fulltext/jyu-theses/fin/2010-M-36884.tsv
../fulltext/jyu-theses/fin/2010-M-36956.tsv
../fulltext/jyu-theses/fin/2010-M-37383.tsv
../fulltext/jyu-theses/fin/2010-M-38622.tsv
../fulltext/jyu-theses/fin/2010-M-40076.tsv
../fulltext/jyu-theses/fin/2010-M-42268.tsv
../fulltext/jyu-theses/fin/2010-M-45150.tsv
../fulltext/jyu-theses/fin/2011-D-25769.tsv
../fulltext/jyu-theses/fin/2011-D-25796.tsv
../fulltext/jyu-theses/fin/2011-D-25799.tsv
../fulltext/jyu-theses/fin/2011-D-25804.tsv
../fulltext/jyu-theses/fin/2011-D-26515.tsv
../fulltext/jyu-theses/fin/2011-D-26534.tsv
../fulltext/jyu-theses/fin/2011-D-26582.tsv
../fulltext/jyu-theses/fin/2011-D-26676.tsv
../fulltext/jyu-theses/fin/2011-D-26810.tsv
../fulltext/jyu-theses/fin/2011-D-27005.tsv
replacing http://www.yso.fi/onto/yso/p9020 with http://www.yso.fi/onto/yso/p39507 http://www.yso.fi/onto/yso/p39511
../fulltext/jyu-theses/fin/2011-D-27118.tsv
../f

../fulltext/jyu-theses/fin/2011-M-27094.tsv
../fulltext/jyu-theses/fin/2011-M-27095.tsv
../fulltext/jyu-theses/fin/2011-M-27096.tsv
../fulltext/jyu-theses/fin/2011-M-27097.tsv
../fulltext/jyu-theses/fin/2011-M-27098.tsv
../fulltext/jyu-theses/fin/2011-M-27100.tsv
../fulltext/jyu-theses/fin/2011-M-27102.tsv
../fulltext/jyu-theses/fin/2011-M-27103.tsv
../fulltext/jyu-theses/fin/2011-M-27104.tsv
../fulltext/jyu-theses/fin/2011-M-27105.tsv
../fulltext/jyu-theses/fin/2011-M-27106.tsv
../fulltext/jyu-theses/fin/2011-M-27107.tsv
../fulltext/jyu-theses/fin/2011-M-27110.tsv
../fulltext/jyu-theses/fin/2011-M-27111.tsv
../fulltext/jyu-theses/fin/2011-M-27112.tsv
../fulltext/jyu-theses/fin/2011-M-27113.tsv
../fulltext/jyu-theses/fin/2011-M-27115.tsv
../fulltext/jyu-theses/fin/2011-M-27122.tsv
../fulltext/jyu-theses/fin/2011-M-27125.tsv
../fulltext/jyu-theses/fin/2011-M-27127.tsv
../fulltext/jyu-theses/fin/2011-M-27139.tsv
../fulltext/jyu-theses/fin/2011-M-27142.tsv
../fulltext/jyu-theses/fin/2011-

../fulltext/jyu-theses/fin/2011-M-36869.tsv
../fulltext/jyu-theses/fin/2011-M-36871.tsv
../fulltext/jyu-theses/fin/2011-M-36872.tsv
../fulltext/jyu-theses/fin/2011-M-36873.tsv
../fulltext/jyu-theses/fin/2011-M-36882.tsv
../fulltext/jyu-theses/fin/2011-M-36886.tsv
../fulltext/jyu-theses/fin/2011-M-36889.tsv
../fulltext/jyu-theses/fin/2011-M-36890.tsv
../fulltext/jyu-theses/fin/2011-M-36894.tsv
../fulltext/jyu-theses/fin/2011-M-36904.tsv
../fulltext/jyu-theses/fin/2011-M-36911.tsv
../fulltext/jyu-theses/fin/2011-M-36912.tsv
../fulltext/jyu-theses/fin/2011-M-36914.tsv
../fulltext/jyu-theses/fin/2011-M-36917.tsv
../fulltext/jyu-theses/fin/2011-M-36920.tsv
../fulltext/jyu-theses/fin/2011-M-36922.tsv
../fulltext/jyu-theses/fin/2011-M-36929.tsv
../fulltext/jyu-theses/fin/2011-M-36936.tsv
../fulltext/jyu-theses/fin/2011-M-36951.tsv
../fulltext/jyu-theses/fin/2011-M-36952.tsv
../fulltext/jyu-theses/fin/2011-M-36957.tsv
../fulltext/jyu-theses/fin/2011-M-36962.tsv
../fulltext/jyu-theses/fin/2011-

...

../fulltext/jyu-theses/fin/2017-M-54161.tsv
../fulltext/jyu-theses/fin/2017-M-54163.tsv
../fulltext/jyu-theses/fin/2017-M-54165.tsv
../fulltext/jyu-theses/fin/2017-M-54166.tsv
../fulltext/jyu-theses/fin/2017-M-54168.tsv
../fulltext/jyu-theses/fin/2017-M-54169.tsv
../fulltext/jyu-theses/fin/2017-M-54172.tsv
../fulltext/jyu-theses/fin/2017-M-54181.tsv
../fulltext/jyu-theses/fin/2017-M-54216.tsv
../fulltext/jyu-theses/fin/2017-M-54218.tsv
../fulltext/jyu-theses/fin/2017-M-54226.tsv
../fulltext/jyu-theses/fin/2017-M-54228.tsv
../fulltext/jyu-theses/fin/2017-M-54234.tsv
../fulltext/jyu-theses/fin/2017-M-54236.tsv
../fulltext/jyu-theses/fin/2017-M-54242.tsv
../fulltext/jyu-theses/fin/2017-M-54246.tsv
../fulltext/jyu-theses/fin/2017-M-54248.tsv
../fulltext/jyu-theses/fin/2017-M-54265.tsv
../fulltext/jyu-theses/fin/2017-M-54269.tsv
../fulltext/jyu-theses/fin/2017-M-54279.tsv
../fulltext/jyu-theses/fin/2017-M-54281.tsv
../fulltext/jyu-theses/fin/2017-M-54283.tsv
../fulltext/jyu-theses/fin/2017-

../fulltext/jyu-theses/fin/2017-M-54679.tsv
../fulltext/jyu-theses/fin/2017-M-54695.tsv
../fulltext/jyu-theses/fin/2017-M-54696.tsv
../fulltext/jyu-theses/fin/2017-M-54697.tsv
../fulltext/jyu-theses/fin/2017-M-54699.tsv
../fulltext/jyu-theses/fin/2017-M-54700.tsv
../fulltext/jyu-theses/fin/2017-M-54702.tsv
../fulltext/jyu-theses/fin/2017-M-54713.tsv
../fulltext/jyu-theses/fin/2017-M-54720.tsv
../fulltext/jyu-theses/fin/2017-M-54724.tsv
../fulltext/jyu-theses/fin/2017-M-54737.tsv
../fulltext/jyu-theses/fin/2017-M-54739.tsv
../fulltext/jyu-theses/fin/2017-M-54743.tsv
../fulltext/jyu-theses/fin/2017-M-54775.tsv
../fulltext/jyu-theses/fin/2017-M-54776.tsv
../fulltext/jyu-theses/fin/2017-M-54813.tsv
../fulltext/jyu-theses/fin/2017-M-54814.tsv
../fulltext/jyu-theses/fin/2017-M-54815.tsv
../fulltext/jyu-theses/fin/2017-M-54821.tsv
../fulltext/jyu-theses/fin/2017-M-54826.tsv
../fulltext/jyu-theses/fin/2017-M-54841.tsv
../fulltext/jyu-theses/fin/2017-M-54863.tsv
../fulltext/jyu-theses/fin/2017-

../fulltext/jyu-theses/fin/2017-M-55150.tsv
../fulltext/jyu-theses/fin/2017-M-55153.tsv
../fulltext/jyu-theses/fin/2017-M-55161.tsv
../fulltext/jyu-theses/fin/2017-M-55166.tsv
../fulltext/jyu-theses/fin/2017-M-55180.tsv
../fulltext/jyu-theses/fin/2017-M-55184.tsv
../fulltext/jyu-theses/fin/2017-M-55187.tsv
../fulltext/jyu-theses/fin/2017-M-55190.tsv
../fulltext/jyu-theses/fin/2017-M-55192.tsv
../fulltext/jyu-theses/fin/2017-M-55194.tsv
../fulltext/jyu-theses/fin/2017-M-55199.tsv
../fulltext/jyu-theses/fin/2017-M-55200.tsv
../fulltext/jyu-theses/fin/2017-M-55202.tsv
../fulltext/jyu-theses/fin/2017-M-55206.tsv
../fulltext/jyu-theses/fin/2017-M-55207.tsv
../fulltext/jyu-theses/fin/2017-M-55208.tsv
../fulltext/jyu-theses/fin/2017-M-55209.tsv
../fulltext/jyu-theses/fin/2017-M-55214.tsv
../fulltext/jyu-theses/fin/2017-M-55219.tsv
../fulltext/jyu-theses/fin/2017-M-55231.tsv
../fulltext/jyu-theses/fin/2017-M-55233.tsv
../fulltext/jyu-theses/fin/2017-M-55245.tsv
../fulltext/jyu-theses/fin/2017-

../fulltext/jyu-theses/fin/2017-M-55911.tsv
../fulltext/jyu-theses/fin/2017-M-55912.tsv
../fulltext/jyu-theses/fin/2017-M-55914.tsv
../fulltext/jyu-theses/fin/2017-M-55918.tsv
../fulltext/jyu-theses/fin/2017-M-55921.tsv
../fulltext/jyu-theses/fin/2017-M-55923.tsv
../fulltext/jyu-theses/fin/2017-M-55930.tsv
../fulltext/jyu-theses/fin/2017-M-55931.tsv
../fulltext/jyu-theses/fin/2017-M-55936.tsv
../fulltext/jyu-theses/fin/2017-M-55937.tsv
../fulltext/jyu-theses/fin/2017-M-55941.tsv
../fulltext/jyu-theses/fin/2017-M-55968.tsv
../fulltext/jyu-theses/fin/2017-M-55970.tsv
../fulltext/jyu-theses/fin/2017-M-55981.tsv
../fulltext/jyu-theses/fin/2017-M-55983.tsv
../fulltext/jyu-theses/fin/2017-M-55991.tsv
../fulltext/jyu-theses/fin/2017-M-55992.tsv
../fulltext/jyu-theses/fin/2017-M-55997.tsv
../fulltext/jyu-theses/fin/2017-M-55998.tsv
../fulltext/jyu-theses/fin/2017-M-56001.tsv
../fulltext/jyu-theses/fin/2017-M-56002.tsv
../fulltext/jyu-theses/fin/2017-M-56004.tsv
../fulltext/jyu-theses/fin/2017-

../fulltext/jyu-theses/fin/2017-M-56315.tsv
../fulltext/jyu-theses/fin/2017-M-56317.tsv
../fulltext/jyu-theses/fin/2017-M-56318.tsv
../fulltext/jyu-theses/fin/2017-M-56319.tsv
../fulltext/jyu-theses/fin/2017-M-56320.tsv
../fulltext/jyu-theses/fin/2017-M-56321.tsv
../fulltext/jyu-theses/fin/2017-M-56322.tsv
../fulltext/jyu-theses/fin/2017-M-56323.tsv
../fulltext/jyu-theses/fin/2017-M-56324.tsv
../fulltext/jyu-theses/fin/2017-M-56331.tsv
../fulltext/jyu-theses/fin/2017-M-56340.tsv
../fulltext/jyu-theses/fin/2017-M-56341.tsv
../fulltext/jyu-theses/fin/2017-M-56343.tsv
../fulltext/jyu-theses/fin/2017-M-56345.tsv
../fulltext/jyu-theses/fin/2017-M-56346.tsv
../fulltext/jyu-theses/fin/2017-M-56349.tsv
../fulltext/jyu-theses/fin/2017-M-56372.tsv
../fulltext/jyu-theses/fin/2017-M-56378.tsv
../fulltext/jyu-theses/fin/2017-M-56381.tsv
../fulltext/jyu-theses/fin/2017-M-56382.tsv
../fulltext/jyu-theses/fin/2017-M-56383.tsv
../fulltext/jyu-theses/fin/2017-M-56386.tsv
../fulltext/jyu-theses/fin/2017-

In [9]:
sync_fulltext_dir('../fulltext/jyu-theses/swe/*.tsv', 'sv')

../fulltext/jyu-theses/swe/2010-M-23239.tsv
../fulltext/jyu-theses/swe/2010-M-24757.tsv
../fulltext/jyu-theses/swe/2010-M-24861.tsv
../fulltext/jyu-theses/swe/2010-M-24881.tsv
../fulltext/jyu-theses/swe/2010-M-25283.tsv
../fulltext/jyu-theses/swe/2010-M-25472.tsv
../fulltext/jyu-theses/swe/2011-D-37086.tsv
../fulltext/jyu-theses/swe/2011-M-25806.tsv
../fulltext/jyu-theses/swe/2011-M-26500.tsv
../fulltext/jyu-theses/swe/2011-M-26714.tsv
../fulltext/jyu-theses/swe/2011-M-26821.tsv
../fulltext/jyu-theses/swe/2011-M-26973.tsv
../fulltext/jyu-theses/swe/2011-M-26981.tsv
../fulltext/jyu-theses/swe/2011-M-26998.tsv
../fulltext/jyu-theses/swe/2011-M-27074.tsv
../fulltext/jyu-theses/swe/2011-M-27218.tsv
../fulltext/jyu-theses/swe/2011-M-27249.tsv
../fulltext/jyu-theses/swe/2011-M-27294.tsv
../fulltext/jyu-theses/swe/2011-M-36516.tsv
../fulltext/jyu-theses/swe/2011-M-36568.tsv
../fulltext/jyu-theses/swe/2011-M-36663.tsv
../fulltext/jyu-theses/swe/2011-M-36797.tsv
../fulltext/jyu-theses/swe/2011-

In [10]:
sync_fulltext_dir('../fulltext/jyu-theses/eng/*.tsv', 'en')

../fulltext/jyu-theses/eng/2010-D-22710.tsv
../fulltext/jyu-theses/eng/2010-D-22733.tsv
../fulltext/jyu-theses/eng/2010-D-22922.tsv
../fulltext/jyu-theses/eng/2010-D-22978.tsv
../fulltext/jyu-theses/eng/2010-D-22979.tsv
../fulltext/jyu-theses/eng/2010-D-22993.tsv
../fulltext/jyu-theses/eng/2010-D-23009.tsv
../fulltext/jyu-theses/eng/2010-D-23094.tsv
../fulltext/jyu-theses/eng/2010-D-23324.tsv
../fulltext/jyu-theses/eng/2010-D-23403.tsv
../fulltext/jyu-theses/eng/2010-D-23585.tsv
../fulltext/jyu-theses/eng/2010-D-23586.tsv
../fulltext/jyu-theses/eng/2010-D-23758.tsv
../fulltext/jyu-theses/eng/2010-D-24186.tsv
../fulltext/jyu-theses/eng/2010-D-24271.tsv
../fulltext/jyu-theses/eng/2010-D-24347.tsv
../fulltext/jyu-theses/eng/2010-D-24404.tsv
../fulltext/jyu-theses/eng/2010-D-24408.tsv
../fulltext/jyu-theses/eng/2010-D-24550.tsv
../fulltext/jyu-theses/eng/2010-D-24575.tsv
../fulltext/jyu-theses/eng/2010-D-24577.tsv
../fulltext/jyu-theses/eng/2010-D-24880.tsv
../fulltext/jyu-theses/eng/2010-

../fulltext/jyu-theses/eng/2011-D-37189.tsv
../fulltext/jyu-theses/eng/2011-D-37190.tsv
../fulltext/jyu-theses/eng/2011-D-37191.tsv
../fulltext/jyu-theses/eng/2011-D-37192.tsv
../fulltext/jyu-theses/eng/2011-D-37195.tsv
../fulltext/jyu-theses/eng/2011-D-37196.tsv
../fulltext/jyu-theses/eng/2011-D-37197.tsv
../fulltext/jyu-theses/eng/2011-D-37198.tsv
../fulltext/jyu-theses/eng/2011-D-37204.tsv
../fulltext/jyu-theses/eng/2011-D-37205.tsv
../fulltext/jyu-theses/eng/2011-D-37311.tsv
../fulltext/jyu-theses/eng/2011-D-37540.tsv
../fulltext/jyu-theses/eng/2011-D-37652.tsv
../fulltext/jyu-theses/eng/2011-D-37907.tsv
../fulltext/jyu-theses/eng/2011-D-40451.tsv
../fulltext/jyu-theses/eng/2011-D-40877.tsv
../fulltext/jyu-theses/eng/2011-D-40911.tsv
../fulltext/jyu-theses/eng/2011-D-42027.tsv
../fulltext/jyu-theses/eng/2011-D-56015.tsv
../fulltext/jyu-theses/eng/2011-M-26593.tsv
../fulltext/jyu-theses/eng/2011-M-26605.tsv
../fulltext/jyu-theses/eng/2011-M-26608.tsv
../fulltext/jyu-theses/eng/2011-

../fulltext/jyu-theses/eng/2012-D-40658.tsv
../fulltext/jyu-theses/eng/2012-D-40659.tsv
../fulltext/jyu-theses/eng/2012-D-40662.tsv
../fulltext/jyu-theses/eng/2012-D-40663.tsv
../fulltext/jyu-theses/eng/2012-D-40741.tsv
../fulltext/jyu-theses/eng/2012-D-40931.tsv
../fulltext/jyu-theses/eng/2012-D-40935.tsv


../fulltext/jyu-theses/eng/2012-D-41013.tsv
../fulltext/jyu-theses/eng/2012-D-41130.tsv
../fulltext/jyu-theses/eng/2012-D-41240.tsv
../fulltext/jyu-theses/eng/2012-D-50565.tsv
../fulltext/jyu-theses/eng/2012-M-37213.tsv
../fulltext/jyu-theses/eng/2012-M-37361.tsv
../fulltext/jyu-theses/eng/2012-M-37368.tsv
../fulltext/jyu-theses/eng/2012-M-37458.tsv
../fulltext/jyu-theses/eng/2012-M-37466.tsv
../fulltext/jyu-theses/eng/2012-M-37489.tsv
../fulltext/jyu-theses/eng/2012-M-37544.tsv
../fulltext/jyu-theses/eng/2012-M-37586.tsv
../fulltext/jyu-theses/eng/2012-M-37605.tsv
../fulltext/jyu-theses/eng/2012-M-37633.tsv
../fulltext/jyu-theses/eng/2012-M-37646.tsv
../fulltext/jyu-theses/eng/2012-M-37713.tsv
../fulltext/jyu-theses/eng/2012-M-37719.tsv
../fulltext/jyu-theses/eng/2012-M-37752.tsv
../fulltext/jyu-theses/eng/2012-M-37768.tsv
../fulltext/jyu-theses/eng/2012-M-37773.tsv
../fulltext/jyu-theses/eng/2012-M-37781.tsv
../fulltext/jyu-theses/eng/2012-M-37782.tsv
../fulltext/jyu-theses/eng/2012-

../fulltext/jyu-theses/eng/2013-D-42249.tsv
../fulltext/jyu-theses/eng/2013-D-42250.tsv
../fulltext/jyu-theses/eng/2013-D-42328.tsv
../fulltext/jyu-theses/eng/2013-D-42334.tsv
../fulltext/jyu-theses/eng/2013-D-42351.tsv
../fulltext/jyu-theses/eng/2013-D-42352.tsv
../fulltext/jyu-theses/eng/2013-D-42369.tsv
../fulltext/jyu-theses/eng/2013-D-42380.tsv
../fulltext/jyu-theses/eng/2013-D-42382.tsv


...

../fulltext/jyu-theses/eng/2016-M-50122.tsv
../fulltext/jyu-theses/eng/2016-M-50125.tsv
../fulltext/jyu-theses/eng/2016-M-50134.tsv
../fulltext/jyu-theses/eng/2016-M-50143.tsv
../fulltext/jyu-theses/eng/2016-M-50159.tsv
../fulltext/jyu-theses/eng/2016-M-50160.tsv
../fulltext/jyu-theses/eng/2016-M-50161.tsv
../fulltext/jyu-theses/eng/2016-M-50200.tsv
../fulltext/jyu-theses/eng/2016-M-50201.tsv
../fulltext/jyu-theses/eng/2016-M-50208.tsv
../fulltext/jyu-theses/eng/2016-M-50222.tsv
../fulltext/jyu-theses/eng/2016-M-50235.tsv
../fulltext/jyu-theses/eng/2016-M-50245.tsv
../fulltext/jyu-theses/eng/2016-M-50251.tsv
../fulltext/jyu-theses/eng/2016-M-50259.tsv
../fulltext/jyu-theses/eng/2016-M-50261.tsv
../fulltext/jyu-theses/eng/2016-M-50274.tsv
../fulltext/jyu-theses/eng/2016-M-50276.tsv
../fulltext/jyu-theses/eng/2016-M-50284.tsv
../fulltext/jyu-theses/eng/2016-M-50302.tsv
../fulltext/jyu-theses/eng/2016-M-50303.tsv
../fulltext/jyu-theses/eng/2016-M-50308.tsv
../fulltext/jyu-theses/eng/2016-

../fulltext/jyu-theses/eng/2017-D-52725.tsv
../fulltext/jyu-theses/eng/2017-D-52741.tsv
../fulltext/jyu-theses/eng/2017-D-52866.tsv
../fulltext/jyu-theses/eng/2017-D-52892.tsv
../fulltext/jyu-theses/eng/2017-D-52955.tsv
../fulltext/jyu-theses/eng/2017-D-52956.tsv
../fulltext/jyu-theses/eng/2017-D-52965.tsv
../fulltext/jyu-theses/eng/2017-D-53013.tsv
../fulltext/jyu-theses/eng/2017-D-53081.tsv
../fulltext/jyu-theses/eng/2017-D-53186.tsv
../fulltext/jyu-theses/eng/2017-D-53226.tsv
../fulltext/jyu-theses/eng/2017-D-53228.tsv
../fulltext/jyu-theses/eng/2017-D-53238.tsv
../fulltext/jyu-theses/eng/2017-D-53242.tsv
../fulltext/jyu-theses/eng/2017-D-53252.tsv
../fulltext/jyu-theses/eng/2017-D-53254.tsv
../fulltext/jyu-theses/eng/2017-D-53264.tsv
../fulltext/jyu-theses/eng/2017-D-53281.tsv
../fulltext/jyu-theses/eng/2017-D-53314.tsv
../fulltext/jyu-theses/eng/2017-D-53375.tsv
../fulltext/jyu-theses/eng/2017-D-53542.tsv
../fulltext/jyu-theses/eng/2017-D-53579.tsv
replacing http://www.yso.fi/onto

../fulltext/jyu-theses/eng/2017-D-54422.tsv
../fulltext/jyu-theses/eng/2017-D-54950.tsv
../fulltext/jyu-theses/eng/2017-D-54965.tsv
../fulltext/jyu-theses/eng/2017-D-55063.tsv
../fulltext/jyu-theses/eng/2017-D-55139.tsv
../fulltext/jyu-theses/eng/2017-D-55140.tsv
../fulltext/jyu-theses/eng/2017-D-55170.tsv
../fulltext/jyu-theses/eng/2017-D-55172.tsv
../fulltext/jyu-theses/eng/2017-D-55196.tsv
../fulltext/jyu-theses/eng/2017-D-55291.tsv
../fulltext/jyu-theses/eng/2017-D-55370.tsv
../fulltext/jyu-theses/eng/2017-D-55373.tsv
../fulltext/jyu-theses/eng/2017-D-55403.tsv
../fulltext/jyu-theses/eng/2017-D-55417.tsv
../fulltext/jyu-theses/eng/2017-D-55478.tsv
../fulltext/jyu-theses/eng/2017-D-55570.tsv
../fulltext/jyu-theses/eng/2017-D-55609.tsv
../fulltext/jyu-theses/eng/2017-D-55610.tsv
../fulltext/jyu-theses/eng/2017-D-55611.tsv
../fulltext/jyu-theses/eng/2017-D-55663.tsv
../fulltext/jyu-theses/eng/2017-D-55694.tsv
../fulltext/jyu-theses/eng/2017-D-55701.tsv
../fulltext/jyu-theses/eng/2017-

../fulltext/jyu-theses/eng/2017-M-54885.tsv
../fulltext/jyu-theses/eng/2017-M-54895.tsv
../fulltext/jyu-theses/eng/2017-M-54900.tsv
../fulltext/jyu-theses/eng/2017-M-54935.tsv
../fulltext/jyu-theses/eng/2017-M-54939.tsv
../fulltext/jyu-theses/eng/2017-M-54941.tsv
../fulltext/jyu-theses/eng/2017-M-54946.tsv
../fulltext/jyu-theses/eng/2017-M-54970.tsv
../fulltext/jyu-theses/eng/2017-M-55035.tsv
../fulltext/jyu-theses/eng/2017-M-55061.tsv
../fulltext/jyu-theses/eng/2017-M-55062.tsv
../fulltext/jyu-theses/eng/2017-M-55092.tsv
../fulltext/jyu-theses/eng/2017-M-55093.tsv
../fulltext/jyu-theses/eng/2017-M-55100.tsv
../fulltext/jyu-theses/eng/2017-M-55136.tsv
../fulltext/jyu-theses/eng/2017-M-55142.tsv
../fulltext/jyu-theses/eng/2017-M-55147.tsv
../fulltext/jyu-theses/eng/2017-M-55182.tsv
../fulltext/jyu-theses/eng/2017-M-55189.tsv
../fulltext/jyu-theses/eng/2017-M-55201.tsv
../fulltext/jyu-theses/eng/2017-M-55203.tsv
../fulltext/jyu-theses/eng/2017-M-55211.tsv
../fulltext/jyu-theses/eng/2017-

../fulltext/jyu-theses/eng/2017-M-55868.tsv
../fulltext/jyu-theses/eng/2017-M-55896.tsv
../fulltext/jyu-theses/eng/2017-M-55907.tsv
../fulltext/jyu-theses/eng/2017-M-55919.tsv
../fulltext/jyu-theses/eng/2017-M-55934.tsv
../fulltext/jyu-theses/eng/2017-M-55961.tsv
../fulltext/jyu-theses/eng/2017-M-56019.tsv
../fulltext/jyu-theses/eng/2017-M-56026.tsv
../fulltext/jyu-theses/eng/2017-M-56063.tsv
../fulltext/jyu-theses/eng/2017-M-56110.tsv
../fulltext/jyu-theses/eng/2017-M-56116.tsv
../fulltext/jyu-theses/eng/2017-M-56117.tsv
../fulltext/jyu-theses/eng/2017-M-56118.tsv
../fulltext/jyu-theses/eng/2017-M-56143.tsv
../fulltext/jyu-theses/eng/2017-M-56169.tsv
../fulltext/jyu-theses/eng/2017-M-56234.tsv
../fulltext/jyu-theses/eng/2017-M-56251.tsv
../fulltext/jyu-theses/eng/2017-M-56271.tsv
../fulltext/jyu-theses/eng/2017-M-56284.tsv
../fulltext/jyu-theses/eng/2017-M-56286.tsv
../fulltext/jyu-theses/eng/2017-M-56316.tsv
../fulltext/jyu-theses/eng/2017-M-56337.tsv
../fulltext/jyu-theses/eng/2017-

In [11]:
sync_fulltext_dir('../fulltext/arto-fi/all/*.tsv', 'fi')

../fulltext/arto-fi/all/1000213.tsv
../fulltext/arto-fi/all/1000231.tsv
../fulltext/arto-fi/all/1000241.tsv
../fulltext/arto-fi/all/1000242.tsv
../fulltext/arto-fi/all/1000249.tsv
../fulltext/arto-fi/all/1000266.tsv
../fulltext/arto-fi/all/1000291.tsv
../fulltext/arto-fi/all/1001336.tsv
../fulltext/arto-fi/all/1001448.tsv
../fulltext/arto-fi/all/1001449.tsv
../fulltext/arto-fi/all/1001637.tsv
../fulltext/arto-fi/all/1001770.tsv
../fulltext/arto-fi/all/1001782.tsv
../fulltext/arto-fi/all/1002714.tsv
../fulltext/arto-fi/all/1002995.tsv
../fulltext/arto-fi/all/1003818.tsv
../fulltext/arto-fi/all/1004024.tsv
../fulltext/arto-fi/all/1004042.tsv
../fulltext/arto-fi/all/1004051.tsv
../fulltext/arto-fi/all/1004208.tsv
../fulltext/arto-fi/all/1004299.tsv
../fulltext/arto-fi/all/1004397.tsv
../fulltext/arto-fi/all/1004464.tsv
../fulltext/arto-fi/all/1004469.tsv
../fulltext/arto-fi/all/1005032.tsv
../fulltext/arto-fi/all/1005036.tsv
../fulltext/arto-fi/all/1005319.tsv
../fulltext/arto-fi/all/1005

../fulltext/arto-fi/all/1028287.tsv
../fulltext/arto-fi/all/1028295.tsv
../fulltext/arto-fi/all/1028298.tsv
../fulltext/arto-fi/all/1028300.tsv
../fulltext/arto-fi/all/1028311.tsv
../fulltext/arto-fi/all/1028325.tsv
../fulltext/arto-fi/all/1028331.tsv
../fulltext/arto-fi/all/1028334.tsv
../fulltext/arto-fi/all/1028452.tsv
../fulltext/arto-fi/all/1028467.tsv
../fulltext/arto-fi/all/1028481.tsv
../fulltext/arto-fi/all/1028510.tsv
../fulltext/arto-fi/all/1028521.tsv
../fulltext/arto-fi/all/1028528.tsv
../fulltext/arto-fi/all/1028561.tsv
../fulltext/arto-fi/all/1028565.tsv
../fulltext/arto-fi/all/1028583.tsv
../fulltext/arto-fi/all/1028614.tsv
../fulltext/arto-fi/all/1028621.tsv
../fulltext/arto-fi/all/1028645.tsv
../fulltext/arto-fi/all/1028656.tsv
../fulltext/arto-fi/all/1028662.tsv
../fulltext/arto-fi/all/1028665.tsv
../fulltext/arto-fi/all/1028675.tsv
../fulltext/arto-fi/all/1028694.tsv
../fulltext/arto-fi/all/1028713.tsv
../fulltext/arto-fi/all/1028729.tsv
../fulltext/arto-fi/all/1028

../fulltext/arto-fi/all/1042150.tsv
../fulltext/arto-fi/all/1042186.tsv
../fulltext/arto-fi/all/1042204.tsv
../fulltext/arto-fi/all/1042211.tsv
../fulltext/arto-fi/all/1042221.tsv
../fulltext/arto-fi/all/1043450.tsv
../fulltext/arto-fi/all/1043452.tsv
../fulltext/arto-fi/all/1043461.tsv
../fulltext/arto-fi/all/1043523.tsv
../fulltext/arto-fi/all/1043608.tsv
../fulltext/arto-fi/all/1043632.tsv
../fulltext/arto-fi/all/1043727.tsv
../fulltext/arto-fi/all/1043777.tsv
../fulltext/arto-fi/all/1043842.tsv
../fulltext/arto-fi/all/1043863.tsv
../fulltext/arto-fi/all/1045190.tsv
../fulltext/arto-fi/all/1045377.tsv
../fulltext/arto-fi/all/1045385.tsv
../fulltext/arto-fi/all/1045405.tsv
../fulltext/arto-fi/all/1045478.tsv
../fulltext/arto-fi/all/1045544.tsv
../fulltext/arto-fi/all/1045648.tsv
../fulltext/arto-fi/all/1045658.tsv
../fulltext/arto-fi/all/1045660.tsv
../fulltext/arto-fi/all/1045666.tsv
../fulltext/arto-fi/all/1045671.tsv
../fulltext/arto-fi/all/1045679.tsv
../fulltext/arto-fi/all/1045

../fulltext/arto-fi/all/1165927.tsv
../fulltext/arto-fi/all/1165930.tsv
../fulltext/arto-fi/all/1166022.tsv
../fulltext/arto-fi/all/1166141.tsv
../fulltext/arto-fi/all/1166413.tsv
../fulltext/arto-fi/all/1166550.tsv
../fulltext/arto-fi/all/1166705.tsv
../fulltext/arto-fi/all/1166791.tsv
../fulltext/arto-fi/all/1166900.tsv
../fulltext/arto-fi/all/1180692.tsv
../fulltext/arto-fi/all/1180696.tsv
../fulltext/arto-fi/all/1180700.tsv
../fulltext/arto-fi/all/1180703.tsv
../fulltext/arto-fi/all/1180711.tsv
../fulltext/arto-fi/all/1180726.tsv
../fulltext/arto-fi/all/1180729.tsv
../fulltext/arto-fi/all/1180732.tsv
../fulltext/arto-fi/all/1180791.tsv
../fulltext/arto-fi/all/1183995.tsv
../fulltext/arto-fi/all/1184001.tsv
../fulltext/arto-fi/all/1184017.tsv
../fulltext/arto-fi/all/1184036.tsv
../fulltext/arto-fi/all/1184046.tsv
../fulltext/arto-fi/all/1184050.tsv
../fulltext/arto-fi/all/1184056.tsv


../fulltext/arto-fi/all/1184063.tsv
../fulltext/arto-fi/all/1184097.tsv
../fulltext/arto-fi/all/1184127.tsv
../fulltext/arto-fi/all/1184221.tsv
../fulltext/arto-fi/all/1184228.tsv
../fulltext/arto-fi/all/1184241.tsv
../fulltext/arto-fi/all/1184277.tsv
../fulltext/arto-fi/all/1184376.tsv
../fulltext/arto-fi/all/1184389.tsv
../fulltext/arto-fi/all/1184503.tsv
../fulltext/arto-fi/all/1184523.tsv
../fulltext/arto-fi/all/1184540.tsv
../fulltext/arto-fi/all/1184710.tsv
../fulltext/arto-fi/all/1184726.tsv
../fulltext/arto-fi/all/1184771.tsv
../fulltext/arto-fi/all/1184827.tsv
../fulltext/arto-fi/all/1184844.tsv
../fulltext/arto-fi/all/1184905.tsv
../fulltext/arto-fi/all/1184922.tsv
../fulltext/arto-fi/all/1184933.tsv
../fulltext/arto-fi/all/1184974.tsv
../fulltext/arto-fi/all/1184978.tsv
../fulltext/arto-fi/all/1185477.tsv
../fulltext/arto-fi/all/1185481.tsv
../fulltext/arto-fi/all/1185496.tsv
../fulltext/arto-fi/all/1185511.tsv
../fulltext/arto-fi/all/1186419.tsv
../fulltext/arto-fi/all/1186

...

../fulltext/arto-fi/all/832491.tsv
../fulltext/arto-fi/all/832577.tsv
../fulltext/arto-fi/all/832587.tsv
../fulltext/arto-fi/all/832595.tsv
../fulltext/arto-fi/all/832603.tsv
../fulltext/arto-fi/all/832618.tsv
../fulltext/arto-fi/all/832727.tsv
../fulltext/arto-fi/all/832747.tsv
../fulltext/arto-fi/all/832764.tsv
../fulltext/arto-fi/all/832784.tsv
../fulltext/arto-fi/all/832910.tsv
../fulltext/arto-fi/all/832949.tsv
../fulltext/arto-fi/all/833084.tsv
../fulltext/arto-fi/all/833085.tsv
../fulltext/arto-fi/all/833114.tsv
../fulltext/arto-fi/all/833127.tsv
../fulltext/arto-fi/all/833128.tsv
../fulltext/arto-fi/all/833141.tsv
../fulltext/arto-fi/all/842391.tsv
../fulltext/arto-fi/all/851734.tsv
../fulltext/arto-fi/all/852225.tsv
../fulltext/arto-fi/all/857683.tsv
../fulltext/arto-fi/all/857685.tsv
../fulltext/arto-fi/all/857689.tsv
../fulltext/arto-fi/all/857702.tsv
../fulltext/arto-fi/all/857763.tsv
../fulltext/arto-fi/all/857766.tsv
../fulltext/arto-fi/all/857769.tsv
../fulltext/arto-fi/

../fulltext/arto-fi/all/878996.tsv
../fulltext/arto-fi/all/878997.tsv
../fulltext/arto-fi/all/879010.tsv
../fulltext/arto-fi/all/879015.tsv
../fulltext/arto-fi/all/879038.tsv
../fulltext/arto-fi/all/879048.tsv
../fulltext/arto-fi/all/879051.tsv
../fulltext/arto-fi/all/879619.tsv
../fulltext/arto-fi/all/879620.tsv
../fulltext/arto-fi/all/879634.tsv
../fulltext/arto-fi/all/879636.tsv
../fulltext/arto-fi/all/879638.tsv
../fulltext/arto-fi/all/879672.tsv
../fulltext/arto-fi/all/880755.tsv
../fulltext/arto-fi/all/880757.tsv
../fulltext/arto-fi/all/880819.tsv
../fulltext/arto-fi/all/880825.tsv
../fulltext/arto-fi/all/880871.tsv
../fulltext/arto-fi/all/880873.tsv
../fulltext/arto-fi/all/880874.tsv
../fulltext/arto-fi/all/880876.tsv
../fulltext/arto-fi/all/880889.tsv
../fulltext/arto-fi/all/880890.tsv
../fulltext/arto-fi/all/880891.tsv
../fulltext/arto-fi/all/880895.tsv
../fulltext/arto-fi/all/880898.tsv
../fulltext/arto-fi/all/880920.tsv
../fulltext/arto-fi/all/880921.tsv
../fulltext/arto-fi/

../fulltext/arto-fi/all/885861.tsv
../fulltext/arto-fi/all/885862.tsv
../fulltext/arto-fi/all/885865.tsv
../fulltext/arto-fi/all/885867.tsv
../fulltext/arto-fi/all/885868.tsv
../fulltext/arto-fi/all/885870.tsv
../fulltext/arto-fi/all/885871.tsv
../fulltext/arto-fi/all/885872.tsv
../fulltext/arto-fi/all/885875.tsv
../fulltext/arto-fi/all/885955.tsv
../fulltext/arto-fi/all/885961.tsv
../fulltext/arto-fi/all/887348.tsv
../fulltext/arto-fi/all/887356.tsv
../fulltext/arto-fi/all/887402.tsv
../fulltext/arto-fi/all/887757.tsv
../fulltext/arto-fi/all/888218.tsv
../fulltext/arto-fi/all/888237.tsv
../fulltext/arto-fi/all/888546.tsv
../fulltext/arto-fi/all/888549.tsv
../fulltext/arto-fi/all/888557.tsv
../fulltext/arto-fi/all/888558.tsv
../fulltext/arto-fi/all/890752.tsv
../fulltext/arto-fi/all/890753.tsv
../fulltext/arto-fi/all/890755.tsv
../fulltext/arto-fi/all/890757.tsv
../fulltext/arto-fi/all/903454.tsv
../fulltext/arto-fi/all/903686.tsv
../fulltext/arto-fi/all/903736.tsv
../fulltext/arto-fi/

../fulltext/arto-fi/all/960175.tsv
../fulltext/arto-fi/all/960298.tsv
../fulltext/arto-fi/all/960317.tsv
../fulltext/arto-fi/all/960326.tsv
../fulltext/arto-fi/all/960426.tsv
../fulltext/arto-fi/all/960880.tsv
../fulltext/arto-fi/all/960887.tsv
../fulltext/arto-fi/all/960904.tsv
../fulltext/arto-fi/all/961376.tsv
../fulltext/arto-fi/all/961394.tsv
../fulltext/arto-fi/all/961401.tsv
../fulltext/arto-fi/all/961429.tsv
../fulltext/arto-fi/all/961434.tsv
../fulltext/arto-fi/all/961447.tsv
../fulltext/arto-fi/all/961459.tsv
../fulltext/arto-fi/all/961462.tsv
../fulltext/arto-fi/all/961533.tsv
../fulltext/arto-fi/all/961591.tsv
../fulltext/arto-fi/all/961601.tsv
../fulltext/arto-fi/all/961648.tsv
../fulltext/arto-fi/all/961879.tsv
../fulltext/arto-fi/all/961940.tsv
../fulltext/arto-fi/all/962483.tsv
../fulltext/arto-fi/all/962525.tsv
../fulltext/arto-fi/all/962600.tsv
../fulltext/arto-fi/all/962605.tsv
../fulltext/arto-fi/all/962698.tsv
../fulltext/arto-fi/all/962704.tsv
../fulltext/arto-fi/

../fulltext/arto-fi/all/968726.tsv
../fulltext/arto-fi/all/968735.tsv
../fulltext/arto-fi/all/968752.tsv
../fulltext/arto-fi/all/968775.tsv
../fulltext/arto-fi/all/968788.tsv
../fulltext/arto-fi/all/968800.tsv
../fulltext/arto-fi/all/968838.tsv
../fulltext/arto-fi/all/968848.tsv
../fulltext/arto-fi/all/969318.tsv
../fulltext/arto-fi/all/969319.tsv
../fulltext/arto-fi/all/969323.tsv
../fulltext/arto-fi/all/969324.tsv
../fulltext/arto-fi/all/969326.tsv
../fulltext/arto-fi/all/970184.tsv
../fulltext/arto-fi/all/970251.tsv
../fulltext/arto-fi/all/970270.tsv
../fulltext/arto-fi/all/970366.tsv
../fulltext/arto-fi/all/970476.tsv
../fulltext/arto-fi/all/970519.tsv
../fulltext/arto-fi/all/970877.tsv
../fulltext/arto-fi/all/970885.tsv
../fulltext/arto-fi/all/970889.tsv
../fulltext/arto-fi/all/970920.tsv
../fulltext/arto-fi/all/970929.tsv
../fulltext/arto-fi/all/971127.tsv
../fulltext/arto-fi/all/971186.tsv
../fulltext/arto-fi/all/971204.tsv
../fulltext/arto-fi/all/971254.tsv
../fulltext/arto-fi/

In [9]:
# This function can be used to update files in the short text corpus format (single TSV file)

def read_short_tsv(fn):
    with open(fn) as tsvf:
        for line in tsvf:
            line = line.strip()
            if '\t' not in line:
                continue
            text, uris = line.split('\t', 1)
            uris = [uri[1:-1] for uri in uris.split()]
            yield (text, uris)

with open('yso-finna-new.tsv', 'w') as newf:
    for text, uris in read_short_tsv('yso-finna.tsv'):
        newuris = []
        for uri in uris:
            for newuri, label in replace_concept((uri, '')):
                if check_concept(newuri):
                    newuris.append(newuri)
        if newuris:
            print("{}\t{}".format(text, '\t'.join(("<{}>".format(uri) for uri in newuris))), file=newf)


FileNotFoundError: [Errno 2] No such file or directory: 'yso-finna.tsv'

In [4]:
sync_fulltext_dir('../../Annif-corpora-restricted/satakunnan-kansa/*/*.tsv', 'fi')

../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT01.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT02.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT03.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT04.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT05.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT06.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT07.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT08.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT09.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT10.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT11.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT12.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT13.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT14.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test1/SKT15.tsv
../../Annif-corpora-restricted/satakunna

../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT35.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT36.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT37.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT38.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT39.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT40.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT41.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT42.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT43.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT44.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT45.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT46.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT47.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT48.tsv
../../Annif-corpora-restricted/satakunnan-kansa/test3/SKT49.tsv
../../Annif-corpora-restricted/satakunna

In [5]:
sync_fulltext_dir('../../Annif-corpora-restricted/vapaakappaleet/fi/*/*.tsv', 'fi')

../../Annif-corpora-restricted/vapaakappaleet/fi/1995/9516722008.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1997/9521105909.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1998/9515612306.tsv
http://urn.fi/URN:NBN:fi:au:cn:56201A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/fi/1998/9515612322.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1998/9515704219.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1998/9517100809.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1998/9525159469.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1998/9789519638034.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1999/9514447220.tsv
http://urn.fi/URN:NBN:fi:au:cn:46624A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/fi/1999/9515319692.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/1999/9515320283.tsv
http://urn.fi/URN:NBN:fi:au:cn:22876A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/fi/1999/9515612950.ts

../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517153791.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296495.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/951729655X.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296630.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296657.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296673.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296681.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296746.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296819.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296851.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296924.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296975.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/9517296991.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2002/951729705X.tsv
../../Annif-corpora-restricted/vap

../../Annif-corpora-restricted/vapaakappaleet/fi/2003/952111360X.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521114207.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521114223.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521114576.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521114592.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521114924.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521115130.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521115149.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521115238.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521115394.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521115491.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521115769.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/9521118121.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2003/952111813X.tsv
../../Annif-corpora-restricted/vap

../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9524532077.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9524680416.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9524770083.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9524770172.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9524770415.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9524770458.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9524770466.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9525210340.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9525210367.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9525565017.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9529175744.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9529180772.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9529916620.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2004/9529917139.tsv
../../Annif-corpora-restricted/vap

http://urn.fi/URN:NBN:fi:au:cn:29098A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9525287130.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9525464210.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9525565033.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9525565041.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529182805.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529183402.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/952918364X.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529193106.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529209878.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529913931.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529917198.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529920970.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2005/9529921411.tsv
http://urn.fi/URN:NBN:fi:au:cn:64556A not a sk

...

../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789518433609.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789519150420.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521149023.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521149108.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521149146.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521426803.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521431401.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521431883.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521432361.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521432910.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521433085.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521433269.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521433290.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789521433

../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523175938.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523175945.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523175969.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523175976.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523176027.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523176102.tsv
http://urn.fi/URN:NBN:fi:au:cn:16552A not a skos:Concept
http://urn.fi/URN:NBN:fi:au:cn:226950A not a skos:Concept
http://urn.fi/URN:NBN:fi:au:cn:226954A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523176126.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523176133.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523176140.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523176164.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789523176188.tsv
../../Annif-corpora-restricted/vapa

../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526684499.tsv
http://urn.fi/URN:NBN:fi:au:cn:193239A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526684505.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526684529.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526721675.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526745091.tsv
http://urn.fi/URN:NBN:fi:au:cn:10099A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526808987.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526834610.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526849560.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526852843.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526852850.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526855783.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789526855790.tsv
../../Annif-corpora-r

../../Annif-corpora-restricted/vapaakappaleet/fi/2018/9789529978274.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789515148933.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789515337238.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789515337320.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789516933873.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789516933880.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789518273083.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789521148309.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789521150180.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789521426728.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789521435188.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789521435669.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789521435782.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789521435

../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529414376.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529414666.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529415625.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529417360.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529417476.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529417940.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529418169.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529420391.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529955480.tsv
../../Annif-corpora-restricted/vapaakappaleet/fi/2019/9789529986286.tsv


In [6]:
sync_fulltext_dir('../../Annif-corpora-restricted/vapaakappaleet/en/*/*.tsv', 'en')

../../Annif-corpora-restricted/vapaakappaleet/en/1998/9515612411.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/1998/9515612489.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/1998/9519767614.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/1999/9515320275.tsv
http://urn.fi/URN:NBN:fi:au:cn:22876A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/en/2000/9515613183.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2000/9515613396.tsv
http://urn.fi/URN:NBN:fi:au:cn:56201A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/en/2000/9521108029.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2000/9524530082.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2001/9524530244.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2001/9524530341.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2002/9515613922.tsv
replacing http://www.yso.fi/onto/yso/p4162 with http://www.yso.fi/onto/yso/p4160
../../Annif-corpora-restricted/vapaakappaleet/

../../Annif-corpora-restricted/vapaakappaleet/en/2006/952485127X.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9524851393.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/952485161X.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9524852209.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9524852292.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/952487007X.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9524870150.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9524870533.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9525350304.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9525583848.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9525583929.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9529957211.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9529966601.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2006/9529966911.tsv
../../Annif-corpora-restricted/vap

../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524855525.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524856058.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524856089.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524856126.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524871532.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524871709.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524871846.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789524871983.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789525672725.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789525672749.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789525672763.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789525672787.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789525672824.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2008/9789526703

../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521052125.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521054211.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521054228.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521054235.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521059438.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521061455.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521061547.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521061820.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521061875.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521061912.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521062414.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521063688.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521063923.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2010/9789521064

../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789521138874.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789521139307.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789521139567.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789521139611.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522161581.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522162434.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522162458.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522171375.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522171467.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522171504.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522171528.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522171566.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522171764.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2011/9789522223

...

../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789526812458.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789526812465.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789526814209.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789526819334.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789526819341.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789526823904.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789527002032.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789527064016.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789527124031.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789529333974.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789529338047.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789529340255.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789529344932.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2014/9789529348

../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526793498.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526811222.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526819303.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526825212.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526828312.tsv
http://www.yso.fi/onto/yso/p105715 has no label
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526829807.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526830636.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526833712.tsv
http://urn.fi/URN:NBN:fi:au:cn:174873A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526835440.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526835457.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526838410.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2015/9789526838427.tsv
../../Annif-corpora-restricted

../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789522951519.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789522951694.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789523172630.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789523173330.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524562430.tsv
http://urn.fi/URN:NBN:fi:au:cn:85028A not a skos:Concept
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524765428.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524765855.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524766128.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524766333.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524766432.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524766654.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789524766678.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2016/9789525260762.tsv
../../A

../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789526868813.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789526871127.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789526871820.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789526876818.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789526881218.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789526886619.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527023167.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527023174.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527200209.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527200216.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527200223.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527282007.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527282014.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2017/9789527282

../../Annif-corpora-restricted/vapaakappaleet/en/2018/9789529405763.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2018/9789529410453.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2018/9789529411269.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789516099227.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789516522671.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789516522695.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789516522718.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789518273076.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789522166975.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789522167040.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789522167088.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789522167132.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789522167149.tsv
../../Annif-corpora-restricted/vapaakappaleet/en/2019/9789522167

In [7]:
sync_fulltext_dir('../../Annif-corpora-restricted/vapaakappaleet/sv/*/*.tsv', 'sv')

../../Annif-corpora-restricted/vapaakappaleet/sv/2002/9524530708.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2002/9524530821.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2003/9517297440.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2003/9524425580.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2003/952442651X.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2003/952453116X.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2004/9517651864.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2004/9521116579.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2004/9524426927.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2004/9524427052.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2004/9524532050.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2005/9517299443.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2005/9521027010.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2005/9524850397.tsv
../../Annif-corpora-restricted/vap

../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515227744.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515227751.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515227799.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515227829.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515227836.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515227874.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228062.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228079.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228291.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228505.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228529.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228543.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228574.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2013/9789515228

../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523143531.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523144330.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523144651.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523144934.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523145108.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523145122.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523145313.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789523145405.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2016/9789527117163.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2017/9786191921539.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2017/9789516933613.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2017/9789516933675.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2017/9789522064189.tsv
../../Annif-corpora-restricted/vapaakappaleet/sv/2017/9789522935

In [8]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/*.tsv', 'fi')

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405442220.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405455489.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405455500.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405455551.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405460539.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405462639.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405481986.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405482346.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1405482354.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/1871912733.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/3833115556.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/3833115815.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/3833116412.tsv
../../Annif-corpora-restr

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510290041.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/951029005X.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510290149.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510290157.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510290440.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510290793.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/951029084X.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510290939.tsv
http://urn.fi/URN:NBN:fi:au:cn:137730A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510291110.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510291323.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510291897.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510292133.tsv
../../Annif-corpora-restricted/kirjaesitte

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/951030381X.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510303828.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510303844.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510304182.tsv
http://urn.fi/URN:NBN:fi:au:cn:158395A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510304190.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510304522.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510305200.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510305219.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510305286.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510305375.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510306029.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510306045.tsv
../../Annif-corpora-restricted/kirjaesitte

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318272.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318361.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318426.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318434.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318566.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318574.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318590.tsv
http://urn.fi/URN:NBN:fi:au:cn:9131A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318604.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318612.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318620.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318671.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9510318892.tsv
../../Annif-corpora-restricted/kirjaesittely

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511189549.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511189557.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/951118959X.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511192477.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511192485.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511192515.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511193198.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511194534.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511195662.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511196073.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511197789.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511197797.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9511197800.tsv
../../Annif-corpora-restr

...

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529906161.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529906222.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529906635.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529907083.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529907144.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529907588.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529907595.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529907922.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529907960.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529907977.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529910311.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529910687.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948529.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948536.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948543.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948567.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948574.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948598.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948819.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948826.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948833.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948864.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529948871.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529949427.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529968411.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529968534.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529968541.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529968565.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529968572.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529968589.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529968596.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529969111.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529969135.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529969722.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529969739.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529969746.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982387.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982394.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982400.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982417.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982431.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982462.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982608.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982837.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982844.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982905.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529982912.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529983117.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999118.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999125.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999132.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999156.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999163.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999187.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999194.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789529999606.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789881633422.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789881633491.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789949139859.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789949156177.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/train/9789

In [9]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/*.tsv', 'fi')

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/6430072600183.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9511175297.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9511196634.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9786164851719.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789177193159.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789177193173.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789178612697.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789188335746.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789510423417.tsv
http://urn.fi/URN:NBN:fi:au:cn:189497A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789510424438.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789510429419.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789510431962.tsv
../../Annif-corpora-rest

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511330523.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511330967.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511330981.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511331346.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511331414.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511331445.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511331483.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511331582.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511332060.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511332084.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511332091.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511332107.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789511332121.tsv

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512401048.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512402915.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512402939.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512406074.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512408849.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512409013.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512409204.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512409969.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512410156.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512410729.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512411146.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512411917.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789512412686.tsv

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516564015.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516564367.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516564718.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516564725.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516564749.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516564954.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516565159.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516565401.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516565579.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516566774.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516567443.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516567627.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789516567726.tsv

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518847154.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518847208.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518847215.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518847239.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518847260.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518847345.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518847352.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518853742.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518854428.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518854473.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518854497.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518854503.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789518854510.tsv

...

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523510968.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523510982.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511002.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511019.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511026.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511033.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511040.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511170.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511187.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511255.tsv
http://urn.fi/URN:NBN:fi:au:cn:236337A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511422.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789523511439.tsv
../../Annif-corpor

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524833530.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524833769.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524861892.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524921237.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524924559.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524924740.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524926065.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524927895.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524928526.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524933261.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524950978.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524952057.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789524952125.tsv

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526353548.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526353555.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526353722.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526353890.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526354316.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526354378.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526354385.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526612119.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526612409.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526614137.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526644158.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526668185.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789526668239.tsv

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527226247.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527226278.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527226285.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527226377.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240175.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240236.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240359.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240519.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240557.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240564.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240571.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240588.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789527240618.tsv

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529414550.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529414796.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529414802.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529414949.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529414994.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529415007.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529415267.tsv
http://urn.fi/URN:NBN:fi:au:cn:11828A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529415281.tsv
http://urn.fi/URN:NBN:fi:au:cn:211112A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529415298.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529415458.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/test/9789529415618.tsv
../../Annif-corpora-restricted/kirjaes

In [10]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/*.tsv', 'fi')

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9511165984.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9516229689.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9516229719.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9516274765.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9518620687.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9781387554133.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9781912296132.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9781912321056.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9782889251018.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789150935448.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789150936469.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789150936582.tsv
../../Annif-corpora-restricted/kirjaesittel

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511296676.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511301592.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511302728.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511306009.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511306719.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511307983.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511308584.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511308775.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511310600.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511310662.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511311126.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511311614.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511321385.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511321415.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511321828.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511321842.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511322160.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511322184.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511322269.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511322955.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511323051.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511323174.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511323198.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511323204.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512090921.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512348749.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512352326.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512359066.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512362189.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512363070.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512363162.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512363605.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512363643.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512363803.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512363926.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789512363940.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513198749.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513198756.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513198770.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513198794.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513198824.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513198947.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513199029.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513199111.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513199432.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513199517.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513199531.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789513245481.tsv
../../Annif-corpora-restrict

...

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526884721.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526890333.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526890418.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526891309.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526891606.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526891712.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526892405.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526893013.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526893020.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526893105.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526893112.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789526893228.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527145333.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527150122.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527150146.tsv
http://urn.fi/URN:NBN:fi:au:cn:185995A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527153277.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527153284.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527153307.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527153314.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527160213.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527160244.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527167519.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789527167557.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/f

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001140.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001157.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001195.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001225.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001270.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001355.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001362.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001386.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001447.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001454.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001508.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528001539.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528073086.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100058.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100188.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100232.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100393.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100423.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100430.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100447.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528100881.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528101291.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528101451.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789528102465.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789529941964.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789529962440.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789529982622.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789529985883.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789529998944.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789949532957.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789949532995.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789949636013.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789949663330.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511325185.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789511336846.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/fin/validate/9789516854543.tsv
../../Annif-corpora-restrict

In [11]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso2021/fin/train/*.tsv', 'fi')

In [12]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/*.tsv', 'fi')

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9519155198.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9781715296353.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789150959437.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510400197.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510429433.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510444658.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510446966.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510447505.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510451281.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510452110.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510452431.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510453964.tsv
../../Annif-corpora-restricted/

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510467176.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510467466.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510467510.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510468319.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510468340.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510469255.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510469309.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510471425.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510473184.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510473313.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510473320.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789510473344.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511346524.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511347545.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511349143.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511350224.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511350262.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511350279.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511350521.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511350668.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511350811.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511350989.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511352228.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511352952.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511366027.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511366133.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511366140.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511366584.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511366676.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511367673.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511367826.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511368205.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511368960.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511369332.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511369547.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511369653.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511381341.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511381358.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511381631.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511381860.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511382126.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511382362.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511382812.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511382997.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511383024.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511383154.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511383307.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789511383345.tsv
../../Annif-corpora-restrict

...

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527313329.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527322369.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527322383.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527322482.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337004.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337189.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337301.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337394.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337424.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337486.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337547.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527337561.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527351932.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527351994.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527352090.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527367087.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527367094.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527367100.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527367117.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527369043.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527371251.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527380246.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527381069.tsv


../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527381328.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527381342.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527381359.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527389317.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527389454.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527396056.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527396063.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527396155.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527396209.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527413029.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789527428016.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528006596.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528035978.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528036111.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528036388.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528036555.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528036647.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528036821.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528039242.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528042631.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528042655.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528042921.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528043065.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789528043218.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529443543.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529443772.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529444199.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529444205.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529444328.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529444915.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529445684.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529446247.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529446513.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529586813.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529603558.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/test/9789529745586.tsv
../../Annif-corpora-restrict

In [13]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/fin/validate/*.tsv', 'fi')

In [14]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/*.tsv', 'en')

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/0973105356.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/0973105399.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/0973716509.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/951025651X.tsv
http://www.yso.fi/onto/yso/p106534 has no label
http://www.yso.fi/onto/yso/p117209 has no label
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9510317853.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9510324868.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9510326674.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9511139940.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9511214764.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9512927934.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9513129357.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9513136159.tsv
../.

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/952484057X.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525180913.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525195112.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525195198.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525308006.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525308081.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/952530812X.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525308138.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525308146.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525308219.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525308324.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525308340.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9525328333.tsv
../../Annif-corpora-restr

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513139469.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513142711.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513148324.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513149536.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513167721.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513195304.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513311797.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513315924.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513318970.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513319137.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513319816.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789513319892.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514483257.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514483523.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514483561.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514483622.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514483929.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514485824.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514487613.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514487637.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514487705.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514487798.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514487859.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514487927.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493553.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493591.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493614.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493652.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493676.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493768.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493782.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493805.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493836.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493881.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493928.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789514493980.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789

...

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523305427.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523307186.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523307308.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523307551.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523307889.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523308282.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523312340.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523312852.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523330443.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523370081.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523370159.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789523370234.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525247213.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525247381.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525247428.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525264784.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525265606.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525308495.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525308501.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525308600.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525308617.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525308730.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525308839.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525308884.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525897043.tsv
http://urn.fi/URN:NBN:fi:au:cn:54402A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525923315.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525923353.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525934601.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525939187.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525944006.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525944068.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525969023.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525969092.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525969115.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525969160.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789525969207.tsv
../../A

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526601229.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526621234.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526649931.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526665405.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526670195.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526670348.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526670386.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526670621.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526670690.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526697260.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526700700.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789526701806.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529237197.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529241804.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529242535.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529248551.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529250769.tsv
http://urn.fi/URN:NBN:fi:au:cn:175914A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529250912.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529253357.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529256853.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529258246.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529258758.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529269747.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/train/9789529271252.tsv
../../

In [15]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/test*.tsv', 'en')

In [16]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/*.tsv', 'en')

../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789510437155.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789511334750.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789512090105.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789512411634.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789512411726.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789512974801.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789513199562.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789513773083.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789513773571.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789516099210.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789516162938.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/eng/validate/9789516196391.tsv
../../Annif-corpora-restrict

In [17]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/train/*.tsv', 'en')

In [18]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/*.tsv', 'en')

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9781467129787.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9781783207428.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9781908612434.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9781910860007.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9788394656508.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789510417386.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789510418512.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789510423714.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789510429198.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789510437155.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789510438169.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789510455197.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499012.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499036.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499159.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499234.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499302.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499340.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499388.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789514499418.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789515100191.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789515100207.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789515100214.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789515122667.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789515683731.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789515951854.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789515951885.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789516162495.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789516162938.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789516196391.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789516534094.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789516630666.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789516933460.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789517463713.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789517657822.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789517657846.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518471106.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518580075.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518580877.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518581003.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518581348.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518581355.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518581560.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518582079.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518775754.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518888386.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789518995213.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789519047782.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521231681.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521231698.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521231735.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521231780.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521231858.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521231995.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521232015.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521232039.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521232053.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521360046.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521362613.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789521362668.tsv
../../Annif-corpora-restrict

...

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789526938806.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789526938875.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789526946900.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527018057.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527054970.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527054987.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067178.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067192.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067345.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067468.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067475.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067567.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067772.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067840.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527067888.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527074664.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527131039.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527131367.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527131473.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527131589.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527159019.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527159026.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527159033.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527167618.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527187272.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527187395.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527187425.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527203026.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527204276.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527225844.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527226117.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527226193.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527226445.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527226544.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527241165.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789527258132.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528006213.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528006787.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528006800.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528006855.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528006923.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528007319.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528007579.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528008156.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528008491.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528009245.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528009306.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528012986.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528035336.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528035619.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528035985.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528043409.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528044598.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528044994.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528051732.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528055693.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528077411.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789528089629.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789529358168.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/test/9789529365746.tsv
../../Annif-corpora-restrict

In [19]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/eng/validate/*.tsv', 'en')

In [20]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/*.tsv', 'sv')

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9510256501.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9511210556.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9513310795.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9513318141.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9513743705.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9515006201.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9515007305.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9515008832.tsv
http://urn.fi/URN:NBN:fi:au:cn:56201A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9515013062.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9515013402.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9515013712.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9515014557.tsv
../../Annif-corpora-restricted/kirjaesittel

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9522131008.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9525045005.tsv
replacing http://www.yso.fi/onto/yso/p5341 with http://www.yso.fi/onto/yso/p5342
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9525045102.tsv
http://urn.fi/URN:NBN:fi:au:cn:27094A not a skos:Concept
http://urn.fi/URN:NBN:fi:au:cn:123387A not a skos:Concept
http://urn.fi/URN:NBN:fi:au:cn:126193A not a skos:Concept
http://urn.fi/URN:NBN:fi:au:cn:126192A not a skos:Concept
http://urn.fi/URN:NBN:fi:au:cn:123390A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9525045129.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9525045218.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9525045226.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9525045242.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9525290360.tsv
../../Annif-corpora-restricted

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515019707.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515019714.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515019738.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020079.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020093.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020116.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020147.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020154.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020185.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020208.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020277.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515020475.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228574.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228581.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228598.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228659.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228864.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228871.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228901.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228932.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228963.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515228970.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515229083.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515229274.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515329950.tsv
http://urn.fi/URN:NBN:fi:au:cn:1436A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515330406.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515331090.tsv
http://urn.fi/URN:NBN:fi:au:cn:27364A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515331588.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515504159.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515506818.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515506856.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515506894.tsv
replacing http://www.yso.fi/onto/yso/p176 with http://www.yso.fi/onto/yso/p15308 http://www.yso.fi/onto/yso/p17710
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515506924.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789515506

...

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789518976625.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789518976731.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789518976854.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789518976878.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789518976885.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789518986655.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789519016191.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789519016559.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789519016597.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789519016696.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789519016702.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789519016719.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521348853.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521353543.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521355035.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521355042.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521356049.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521356070.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521356087.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521356353.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521358975.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521359156.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521410147.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789521412554.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045369.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045390.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045406.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045420.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045437.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045444.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045451.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045468.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045499.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045505.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045529.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789525045536.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526727226.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526727233.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526727240.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526727264.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526727271.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526727288.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526727295.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526734002.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526734026.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526735948.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526740447.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789526745633.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529345670.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529350773.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529354870.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529354993.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529360192.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529364015.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529365111.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529366279.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529374199.tsv
http://urn.fi/URN:NBN:fi:au:cn:50416A not a skos:Concept
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529375172.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529376681.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/train/9789529377923.tsv
../../A

In [21]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/*.tsv', 'sv')

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789515247964.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789515248022.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789515248053.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789515248336.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789521356032.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789521365539.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789522312655.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789523332010.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789523332041.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789523430655.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789526918808.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789526918815.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/test/9789527067765.tsv

In [22]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/*.tsv', 'sv')

../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789511334781.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789511334798.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515244079.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515244086.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515244130.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515245847.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515246363.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515246448.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515246462.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515246486.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515246608.tsv
../../Annif-corpora-restricted/kirjaesittelyt/yso/swe/validate/9789515246912.tsv
../../Annif-corpora-restrict

In [23]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/train/*.tsv', 'sv')

In [24]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/*.tsv', 'sv')

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789197361019.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511297017.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511304227.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511334767.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511334781.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511334798.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511337171.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511339052.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789511391852.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789513766900.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789513777159.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789513957247.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515236937.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515236944.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515236951.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515237101.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515237149.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515237156.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515237163.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515238054.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515238061.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515238122.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515239662.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515240125.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515243379.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515243386.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515243447.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515243461.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515244079.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515244086.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515244130.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515245847.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515246363.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515246448.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515246462.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515246486.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515247964.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515247995.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515248022.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515248053.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515248060.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515248091.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515248336.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515249203.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515249227.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515249296.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515249357.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515250292.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508416.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508423.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508430.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508447.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508461.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508478.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508485.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508522.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508560.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508577.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508584.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789515508614.tsv
../../Annif-corpora-restrict

...

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527100165.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527100851.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527148051.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527167274.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527167434.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527167533.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527220085.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527224021.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527224052.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527224069.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527224144.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527224151.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527318041.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527320013.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789527320136.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528005223.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528008347.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528018186.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528019343.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528021940.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528022091.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528036067.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789528090212.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529283446.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529379613.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529380732.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529381982.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529382262.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529384297.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529386505.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529388059.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529390694.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529392155.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529393572.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529396481.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529396535.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529411702.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529414321.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529416493.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529416769.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529419029.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529419562.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529419852.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529420346.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529422685.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529424368.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529424528.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529424863.tsv
../../Annif-corpora-restrict

../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529437269.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529439379.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529440160.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529440757.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529444182.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529503896.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529600250.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529622153.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529745456.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529745548.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529745869.tsv
../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/test/9789529834938.tsv
../../Annif-corpora-restrict

In [25]:
sync_fulltext_dir('../../Annif-corpora-restricted/kirjaesittelyt2021/yso/swe/validate/*.tsv', 'sv')